# Model Training (Adapted from Yasona Neocleous' Code)

In [1]:
pip install torch

In [2]:
pip install torchvision

Note: you may need to restart the kernel to use updated packages.


In [3]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.optim import lr_scheduler
import torch.backends.cudnn as cudnn
import numpy as np
import torchvision
from torchvision import datasets, models, transforms
from torch.utils.data import DataLoader
from torchvision.datasets import ImageFolder
import matplotlib.pyplot as plt
import time
import os
from PIL import Image
from tempfile import TemporaryDirectory
from pathlib import Path
cudnn.benchmark = True
plt.ion()   # interactive mode
from tqdm import tqdm
import torchvision.models as models

In [6]:
# Data augmentation and normalization for training
# Just normalization for validation
data_transforms = {
    'Train_sorted': transforms.Compose([
        transforms.Resize((256, 256)),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'Validation_sorted': transforms.Compose([
        transforms.Resize((256, 256)),
        #transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
}


data_dir = r'C:\Users\jcocco\Dropbox\SkinLesionCode' #CHANGE DATA DIRECTORY
image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x),
                                          data_transforms[x])
                  for x in ['Train_sorted', 'Validation_sorted']}
dataloaders = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=32,
                                             shuffle=True, num_workers=2)
              for x in ['Train_sorted', 'Validation_sorted']}
dataset_sizes = {x: len(image_datasets[x]) for x in ['Train_sorted', 'Validation_sorted']}
class_names = image_datasets['Train_sorted'].classes
print(class_names)

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

['AK', 'BCC', 'BKL', 'DF', 'MEL', 'NV', 'SCC', 'VASC']


In [7]:
def train_model(model, criterion, optimizer, scheduler, num_epochs = None, model_name = None, patience = None):
    since = time.time()

    # Initialize lists to store loss and accuracy values
    train_loss_history = []
    train_acc_history = []
    val_loss_history = []
    val_acc_history = []

    best_loss = float('inf')  # Track the best validation loss
    epochs_no_improve = 0  # Counter for early stopping

    for epoch in tqdm(range(num_epochs)):
        print(f'Epoch {epoch+1}/{num_epochs}')
        print('-' * 10)

        for phase in ['Train_sorted', 'Validation_sorted']:
            if phase == 'Train_sorted':
                model.train()  # Set model to training mode
            else:
                model.eval()   # Set model to evaluation mode

            running_loss = 0.0
            running_corrects = 0

            for inputs, labels in dataloaders[phase]:
                print(f"Batch fetched for phase: {phase}")
                inputs = inputs.to(device)
                labels = labels.to(device)

                optimizer.zero_grad()

                with torch.set_grad_enabled(phase == 'Train_sorted'):
                    outputs = model(inputs)
                    _, preds = torch.max(outputs, 1)
                    loss = criterion(outputs, labels)
                    print(f"Loss: {loss.item()}")

                    if phase == 'Train_sorted':
                        loss.backward()
                        optimizer.step()

                print(f"Batch processed for phase: {phase}")

                running_loss += loss.item() * inputs.size(0)
                running_corrects += torch.sum(preds == labels.data)
            
            epoch_loss = running_loss / dataset_sizes[phase]  # Calculate epoch loss
            epoch_acc = running_corrects.double() / dataset_sizes[phase]  # Calculate epoch accuracy

            print(f'{phase} Loss: {epoch_loss:.4f} Acc: {epoch_acc:.4f}')

            if phase == 'Train_sorted':
                train_loss_history.append(epoch_loss)
                train_acc_history.append(epoch_acc)
            else:
                val_loss_history.append(epoch_loss)
                val_acc_history.append(epoch_acc)

                # Check for early stopping based on validation loss
                if epoch_loss < best_loss:
                    best_loss = epoch_loss
                    epochs_no_improve = 0  # Reset counter if validation loss improves
                else:
                    epochs_no_improve += 1  # Increment if no improvement

         # Call scheduler.step after the loss has been calculated for each epoch
        if phase == 'Train_sorted':  # Only step scheduler for training phase
            scheduler.step(epoch_loss)

        # Save model checkpoint after each epoch
        model_save_path = f'model_{model_name}_epoch_{epoch+1}_3.pth'
        torch.save(model, model_save_path)
        print(f'Model saved to {model_save_path}')

        # Save training history after each epoch
        history_save_path = f'training_history_{model_name}_epoch_{epoch+1}_3.pth'
        torch.save({
            'train_loss': train_loss_history,
            'train_acc': train_acc_history,
            'val_loss': val_loss_history,
            'val_acc': val_acc_history
        }, history_save_path)
        print(f'Training history saved to {history_save_path}')

        # Check early stopping condition
        if epochs_no_improve >= patience:
            print(f'Early stopping triggered after {epochs_no_improve} epochs without validation loss improvement.')
            break

    time_elapsed = time.time() - since
    print(f'Training complete in {time_elapsed // 60:.0f}m {time_elapsed % 60:.0f}s')
    print(f'Best Validation Loss: {best_loss:.4f}')

    return model




# Model 1

In [9]:
save_dir = data_dir # CHANGE DIRECTORY

# creating best model
model_conv = torchvision.models.efficientnet_b7(weights='IMAGENET1K_V1')
for i, param in enumerate(model_conv.parameters()):
    if i<237:
        param.requires_grad = False
    else:
        param.requires_grad = True 

num_ftrs = model_conv.classifier[1].in_features

model_conv.classifier = nn.Sequential(
nn.Dropout(p=0.5, inplace=True),
nn.Linear(in_features=num_ftrs, out_features=8, bias=True))

model_conv = model_conv.to(device)

criterion = nn.CrossEntropyLoss()

# Observe that all parameters are being optimized
optimizer_ft = optim.Adam(model_conv.parameters(), lr=5e-5)

# Decay LR by a factor of 0.1 every 7 epochs
exp_lr_scheduler = lr_scheduler.StepLR(optimizer_ft, step_size=5, gamma=0.5)

# Training best model (first model)
model_conv = train_model(model_conv, criterion, optimizer_ft, exp_lr_scheduler,
                       num_epochs=10, model_name = 'b7', patience = 5)


  0%|          | 0/15 [00:00<?, ?it/s]

Epoch 0/14
----------
Batch fetched for phase: Train_sorted
Loss: 2.07232928276062
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.134550094604492
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.1009883880615234
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.0998034477233887
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.08878231048584
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.0599968433380127
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.019460439682007
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.1013052463531494
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.067734956741333
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 2.016377925872

  7%|▋         | 1/15 [2:49:24<39:31:37, 10164.14s/it]


Epoch 1/14
----------
Batch fetched for phase: Train_sorted
Loss: 0.8186803460121155
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.34306690096855164
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.5385042428970337
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.252996027469635
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.4332379698753357
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.39289745688438416
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.2203088402748108
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.42120251059532166
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.6059160232543945
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.51

 13%|█▎        | 2/15 [5:37:59<36:35:58, 10135.25s/it]

...

 93%|█████████▎| 14/15 [39:49:43<2:50:28, 10228.48s/it]

Loss: 0.5220386385917664
Batch processed for phase: Validation_sorted
Validation_sorted Loss: 0.9727 Acc: 0.7989

Epoch 14/14
----------
Batch fetched for phase: Train_sorted
Loss: 0.0019908053800463676
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.0008170960936695337
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.004881375003606081
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.006970704533159733
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.00044630200136452913
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.00011429709411459044
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.02039363794028759
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.017332643270492554
Batch processed for phase: Train_sorted
Batch fetched for 

100%|██████████| 15/15 [42:38:04<00:00, 10232.28s/it]  


Training complete in 2558m 4s
Best val Acc: 0.810000
Training history saved to training_history_b7.pth


Entire model saved to pytorch_finetuned_b7_full.pth


# Model 2

In [10]:
# Creating second model
model_conv = torchvision.models.efficientnet_b6(weights='IMAGENET1K_V1')
for i, param in enumerate(model_conv.parameters()):
    if i<237:
        param.requires_grad = False
    else:
        param.requires_grad = True 

    

num_ftrs = model_conv.classifier[1].in_features

model_conv.classifier = nn.Sequential(nn.Dropout(0.4),
                                         nn.Linear(num_ftrs, 128), 
                                         nn.ReLU(),
                                         nn.Dropout(0.4),
                                         nn.Linear(128, 16),
                                         nn.ReLU(),
                                         nn.Linear(16, len(class_names)))

        
for name, param in model_conv.named_parameters():
    print(name,param.requires_grad)  


model_conv = model_conv.to(device)

criterion = nn.CrossEntropyLoss()

# Observe that all parameters are being optimized
optimizer_ft = optim.Adam(model_conv.parameters(), lr=1e-5)

# Decay LR by a factor of 0.1 every 7 epochs
exp_lr_scheduler = lr_scheduler.StepLR(optimizer_ft, step_size=5, gamma=0.5)

# Training second model
model_conv = train_model(model_conv, criterion, optimizer_ft, exp_lr_scheduler,
                       num_epochs=15, model_name = 'b6', patience = 5)


Downloading: "https://download.pytorch.org/models/efficientnet_b6_lukemelas-24a108a5.pth" to C:\Users\jcocco/.cache\torch\hub\checkpoints\efficientnet_b6_lukemelas-24a108a5.pth
100%|██████████| 165M/165M [00:02<00:00, 80.4MB/s] 


features.0.0.weight False
features.0.1.weight False
features.0.1.bias False
features.1.0.block.0.0.weight False
features.1.0.block.0.1.weight False
features.1.0.block.0.1.bias False
features.1.0.block.1.fc1.weight False
features.1.0.block.1.fc1.bias False
features.1.0.block.1.fc2.weight False
features.1.0.block.1.fc2.bias False
features.1.0.block.2.0.weight False
features.1.0.block.2.1.weight False
features.1.0.block.2.1.bias False
features.1.1.block.0.0.weight False
features.1.1.block.0.1.weight False
features.1.1.block.0.1.bias False
features.1.1.block.1.fc1.weight False
features.1.1.block.1.fc1.bias False
features.1.1.block.1.fc2.weight False
features.1.1.block.1.fc2.bias False
features.1.1.block.2.0.weight False
features.1.1.block.2.1.weight False
features.1.1.block.2.1.bias False
features.1.2.block.0.0.weight False
features.1.2.block.0.1.weight False
features.1.2.block.0.1.bias False
features.1.2.block.1.fc1.weight False
features.1.2.block.1.fc1.bias False
features.1.2.block.1.fc2

  0%|          | 0/20 [00:00<?, ?it/s]

Epoch 0/19
----------
Batch fetched for phase: Train_sorted
Loss: 7.550522804260254
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 8.004898071289062
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.7891435623168945
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.556713104248047
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.8890767097473145
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.987123966217041
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.756283760070801
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.800232887268066
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 8.133099555969238
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 7.891171455383

  5%|▌         | 1/20 [2:08:06<40:33:57, 7686.21s/it]

...

 95%|█████████▌| 19/20 [40:17:10<2:06:21, 7581.05s/it]


Epoch 19/19
----------
Batch fetched for phase: Train_sorted
Loss: 0.20062009990215302
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.15251325070858002
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.21870577335357666
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.08227802067995071
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.10713018476963043
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.20293419063091278
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.11692818999290466
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.43774065375328064
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Loss: 0.1443866789340973
Batch processed for phase: Train_sorted
Batch fetched for phase: Train_sorted
Los

100%|██████████| 20/20 [42:25:14<00:00, 7635.72s/it]  

Loss: 0.3876570761203766
Batch processed for phase: Validation_sorted
Validation_sorted Loss: 0.7762 Acc: 0.7471

Training complete in 2545m 15s
Best val Acc: 0.749737
Training history saved to training_history_b6.pth


Entire model saved to pytorch_finetuned_b6_full.pth


In [ ]:
# Load pre-trained EfficientNet B5 model
model_conv = torchvision.models.efficientnet_b5(weights='IMAGENET1K_V1')

# Freeze the initial layers (first 237 layers)
for i, param in enumerate(model_conv.parameters()):
    if i < 237:
        param.requires_grad = False
    else:
        param.requires_grad = True

# Modify the fully connected layer to match the number of classes
num_ftrs = model_conv.classifier[1].in_features

# Modify the classifier layers
model_conv.classifier = nn.Sequential(
    nn.Dropout(0.4),
    nn.Linear(num_ftrs, 128),
    nn.ReLU(),
    nn.Dropout(0.4),
    nn.Linear(128, 16),
    nn.ReLU(),
    nn.Linear(16, len(class_names))  # Number of output classes
)

# Move the model to the device (GPU/CPU)
model_conv = model_conv.to(device)

# Define the loss function and optimizer
criterion = nn.CrossEntropyLoss()

# Use Adam optimizer with a learning rate of 1e-5
optimizer_ft = optim.Adam(model_conv.parameters(), lr=1e-6)

# Decay the learning rate by a factor of 0.5 every 2 epochs if the validation loss doesn't improve
exp_lr_scheduler = lr_scheduler.ReduceLROnPlateau(optimizer_ft, 'min', factor=0.5, patience=2)

# Train the model using early stopping
model_conv = train_model(model_conv, criterion, optimizer_ft, exp_lr_scheduler,
                            num_epochs=20, model_name='b5', patience=5)